#### This notebook was created for the NeIC 2022 Quantum Computing Workshop held on 01.06.2022. Based on previous year notebooks.

# **Quantum "Hello World!": Superposition and Measurement**

#### Jake Muff - CSC IT Center for Science, FI

In this workshop we will be writing and executing a real quantum algorithm using jupyter notebooks (python) and  [myQLM](https://myqlm.github.io/index.html).

We will be creating a **superposition state** using single qubit and a **Hadamard** gate. We will then observe the resulting qubit state. 

After this, there will be a (more) hands on task: Create a Quantum Random Number generator!


## First step: Create a program

The first step towards creating a quantum circuit on *myQLM* is to create a variable that will hold a corresponding **program**.
This is done by:

+ importing the functions from **qat.lang.AQASM** -library
+ creating a program instance

First we must import the functions from `qat.lang.AQASM`:

In [ ]:
from qat.lang.AQASM import Program, H
# In practice we can use `import *` to import all functions from the library. However we do not need to here. 

Now we can create a **program object**.

To do so you need:
+ to define a name for the variable of your program
+ to call from the AQASM library the function **Program**

The program object is used to store the quantum circuits and contains a list of all the quantum operations before on the circuit as well as the qubits they are applied to. 

In [ ]:
prog = Program()

## Second step: Allocate the qubits


We need to only one qubit in our program.

We need to:
+ define the name for our register of qubits
+ call the function **qalloc** ("qubit allocate") on our program
+ define the number of qubits we want

The following cell allocates (creates) one qubit to our program:

In [ ]:
qbits = prog.qalloc(1) # allocating 1 qubit for now

## Third step: Applying gates

Now, we can have access to our qubit using the name of the register.

Registers behave like python list/arrays, for example if you named your register QUBIT_REGISTER:
+ QUBIT_REGISTER[0] is the first qubit.
+ QUBIT_REGISTER[1] is the second qubit.

To *create a superposition*, we simply need to **apply** the Hadamard gate to the qubit:
To do so we need to:
+ specify on which program we wish to apply our gate
+ specify the gate we wish to apply
+ specify the name of the qubit register we wish to apply the gate
+ specify the index of the qubit inside the register


The following cell applies the Hadamard gate (**H**) to the first (and in this case only) qubit in the register:

In [ ]:
prog.apply(H, qbits[0]) 

Mathematically, what have we just done? The hadamard gate 

Now we have a program where Hadamard gate is applied to one qubit.

We now need to create the **quantum circuit** associated with this program.

## Fourth step: Create and visualize the circuit

The QLM is based on an object called a **circuit**.

Once a program is created it is possible to generate the circuit from it.

A circuit can therefore be:
+ executed
+ optimized
+ used to create other circuits

To create your circuit you will need to:
+ define the name of your cicuit
+ call the function **to_circ** on your program

The following cell creates a circuit based on our program:

In [ ]:
circuit = prog.to_circ()

We can now vizualize this circuit using the following command
+ %qatdisplay CIRCUIT_NAME

Vizualizing the circuit can be a useful tool to quickly verify that we have created the correct circuit.

In [ ]:
%qatdisplay circuit

## Fifth step: Execute and measure the circuit

We now have a circuit object. This circuit can be made into a **job** that can be executed by a 'quantum processing unit', *i.e.*, a **QPU**. In *myQLM* the QPU is a classical simulator that *mimics (emulates) a real physical QPU*. It does this by keeping track of all the possible qubit states and their evolution. This requires a lot of memory and is in general possible only for a small number of qubits (< 50).

To create a job we need to:
+ define the name for our job
+ call the method **to_job** on a circuit

First, we will call `to_job` without any parameters:

In [ ]:
job1 = circuit.to_job() # leaving the arguments empty corresponds to an infite number of shots
# Meaning we would get a theoretical result

The arguments given to `to_job()` method define the kind information we want to extract from our qubits after the circuit is executed. More precisely, whether we want to **emulate measurement** or take advantage of the fact that we are only simulating one, and thus have information of the **full distribution of states**. Giving no arguments as in the previous cell, defaults to the latter case, full distribution.

**In reality**, when measuring physical qubits one observes only definite values corresponding to zeros and ones; the *probability amplitudes* describing the quantum state cannot be measured. 

To simulate this in pyAQASM, we need to give the `circuit.to_job()` method an argument: `nbshots`, and set it to equal the number of times we want to execute and measure the circuit. The following cell creates a job that corresponds to emulating **5** repeated measurements. 

In [ ]:
job2 = circuit.to_job(nbshots = 5)
# Now we are running with a finite number of shots

To run our job we need to use a simulator. Here is where we diverge from running this on a real quantum computer. The simulator that *myQLM* uses is called `PyLinalg()` and is written in python. More information can be found [here](https://myqlm.github.io/myqlm_specific/qat-pylinalg.html). 

The *QPU* or Quantum Processing Unit simulates the execution of quantum jobs with classical simulation methods. 

In [ ]:
from qat.pylinalg import PyLinalg
#from qat.qpus import PyLinalg another way to import it. 

qpu = PyLinalg() # PyLinalg comes from Python Linear algebra - the method used to simulate quantum mechanics

We can now submit the job to our simulator.

To do so we need to use the function **submit** on our QPU and pass our job as a parameter. The output will be stored in the **result** object:

In [ ]:
result1 = qpu.submit(job1) # results of the 'full distribution' job

result2 = qpu.submit(job2) # results of the 'measurement emulation' job

## Sixth step: Read out the result

The result object is an array of **samples**. Samples hold information of the qubit register after the execution. The type of information depends again on the job that was submitted. Let us look at the two cases:
+ **full distribution**: samples hold probability amplitudes (and probabilities) of each possible state
+ **measurement emulation**: samples hold statistical probabilities of states, calculated from repeated measurements

The samples are conveniently accessed using a *for loop*. The following cell displays the result from the evaluation of the *full distribution* job, job1:

In [ ]:
for sample in result1:
    print("state:", sample.state, "probability amplitude:", sample.amplitude, "probability:", sample.probability)

We see that the qubit is in an equal superposition of 0 and 1. Measuring the qubit would give |0> with 50% and |1> with 50%. 

Note that probabilities are connected to probability amplitudes by $P_\alpha=|\alpha|^2$, where $\alpha$ is a probability amplitude of a state and $P_\alpha$ is probability that this state is observed in a measurement.

Finally, let us look at the result of the job that emulated 5 repeated measurements. 

In [ ]:
for sample in result2:
    print("state:", sample.state, "probability amplitude:", sample.amplitude, "probability:", sample.probability)

Now, just like with real world quantum systems, the probability amplitudes of the states are unknown. The result consists of the statistical probabilities obtained from 5 repeated measurements. Because we only have 5 measurements the results are largely random and not converged. 

If we increase the number of `nbshots`, what would we see? Try for yourself!

In [ ]:
job3 = circuit.to_job(nbshots = 1000)

result3 = qpu.submit(job3)

for sample in result3:
    print("state:", sample.state, "probability:", sample.probability)

## Summary


1. Create a program with `Program()`
2. Allocate how many qubits you want and/or need with `qalloc(x)`
3. Apply the gates to your program with `apply(gate, qubits[i]`
4. Create the circuit with `to_circ()`
5. Vizualize the circuit with `qatdisplay circuit`
6. Create your job (`to_job()`)and decide how many 'shots' you want `nbshots=`
7. Define a QPU and submit the job to it `qpu.submit(job)`
7. Print your results

In one cell this looks like:

In [ ]:
from qat.lang.AQASM import Program, H
from qat.pylinalg import PyLinalg

qpu = PyLinalg()

prog = Program()

qbits = prog.qalloc(1)

prog.apply(H, qbits[0])

circuit = prog.to_circ()

job3 = circuit.to_job(nbshots = 100)

result3 = qpu.submit(job3)

for sample in result3:
    print("state:", sample.state, "probability:", sample.probability)
    
%qatdisplay circuit

## Also check out

- https://quantumtictactoe.com/



## Don´t forget

Save your own copy of the notebook!